In [11]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder, StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split, GridSearchCV
import networkx as nx
from sklearn.neighbors import NearestNeighbors, KNeighborsRegressor
from torch_geometric.data import Data
from torch_geometric.utils import to_networkx
import torch
import matplotlib.pyplot as plt
from sklearn.model_selection import GridSearchCV, KFold
from sklearn.metrics import make_scorer, mean_squared_error

import torch.nn.functional as F
from torch_geometric.nn import GATConv, GCNConv, SAGEConv,GraphConv, GINConv, GATConv
from torch_geometric.loader import DataLoader
from sklearn.metrics import root_mean_squared_error
from sklearn.metrics import r2_score
from torch.optim.lr_scheduler import StepLR
import torch.optim as optim
from hyperopt import fmin, tpe, hp, Trials
from torch.utils.data import Dataset

import sys
import os

# Add the parent directory to sys.path
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), os.pardir)))
from pre_processing import preprocess_data

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [12]:
def load_data():
    dataset = pd.read_excel(r"globalterrorismdb_2021Jan-June_1222dist.xlsx") # 2021-2021 June
    return dataset

- Converts tabular data into a graph using the k-Nearest Neighbors (k-NN) algorithm. The graph nodes represent rows of the dataset, and edges represent k-NN connections. It outputs a torch_geometric.data.Data object containing node features, edges, and target labels.

In [13]:
def create_graph_from_data(X, y, k=6, metric="euclidean"):
    # Number of nodes (rows)
    num_nodes = X.shape[0]

    knn = NearestNeighbors(n_neighbors=k + 1, metric=metric)
    knn.fit(X)
    distances, indices = knn.kneighbors(X)

    graph = nx.Graph()

    # Add nodes with features
    for i in range(num_nodes):
        graph.add_node(i, x=X[i])

    # Add edges based on KNN
    for i in range(num_nodes):
        for j in indices[i][1:]:  # Skip the first neighbor (self-loop)
            graph.add_edge(i, j)

    # Step 3: Extract edge index and node features
    edge_index = torch.tensor(list(graph.edges)).t().contiguous()
    # Add reverse edges to make it undirected
    edge_index = torch.cat([edge_index, edge_index.flip(0)], dim=1)
    node_features = torch.tensor(np.array([graph.nodes[i]['x'] for i in range(num_nodes)]), dtype=torch.float)
    targets = torch.tensor(y, dtype=torch.float)

    # Step 4: Create PyTorch Geometric Data object
    data = Data(x=node_features, edge_index=edge_index, y=targets)

    return data

- Splits the graph data into training and validation sets by creating boolean masks based on a random permutation of nodes.

In [14]:
def split_graph_data(dataset):
    torch.manual_seed(42)

    indices = torch.randperm(dataset.num_nodes)

    train_size = int(dataset.num_nodes * 0.8)

    # Create boolean masks
    train_mask = torch.zeros(dataset.num_nodes, dtype=torch.bool)
    val_mask = torch.zeros(dataset.num_nodes, dtype=torch.bool)

    # set masks
    train_mask[indices[:train_size]] = True
    val_mask[indices[train_size:]] = True

    return train_mask, val_mask

## Data Loading and Preprocessing

In [15]:
dataset = load_data()
X, y, dataset = preprocess_data(dataset)

dataset = [create_graph_from_data(X, y)]  # Wrap the single graph in a list
train_mask, val_mask = split_graph_data(dataset[0])

print(f"Dataset\n------------------------")
print(f"Data structure: {dataset[0]}")  # Access the single Data object
print(f"Number of features: {dataset[0].num_features}")
print(f"Number of edges: {dataset[0].num_edges}")
print(f"Number of Nodes: {dataset[0].num_nodes}")
print(f"No of Train nodes: {train_mask.sum()}")
print(f"No of Val nodes: {val_mask.sum()}")

print(f"no of graphs: {len(dataset)}")



Dataset
------------------------
Data structure: Data(x=[2689, 25], edge_index=[2, 22812], y=[2689])
Number of features: 25
Number of edges: 22812
Number of Nodes: 2689
No of Train nodes: 2151
No of Val nodes: 538
no of graphs: 1


## 3) GNN
## Hyperparameter Tuning

In [16]:
class GNNModel(torch.nn.Module):
    def __init__(self, in_channels, hidden_channel1=64, hidden_channel2=64, out_channels=1, dropout=0.3, conv_type="SAGEConv"):
        super(GNNModel, self).__init__()
        
        self.conv_type = conv_type
        conv_layer = {"SAGEConv": SAGEConv, "GCNConv": GCNConv, "GATConv": GATConv}[conv_type]

        self.conv1 = conv_layer(in_channels, hidden_channel1)
        self.conv2 = conv_layer(hidden_channel1, hidden_channel2)
        
        self.dropout = torch.nn.Dropout(p=dropout)
        
        # Projection layer for skip connection
        self.projection = torch.nn.Linear(in_channels, hidden_channel2)
        
        # Fully connected layers for output
        self.fc1 = torch.nn.Linear(hidden_channel2, 64)
        self.fc2 = torch.nn.Linear(64, out_channels)
        
    def forward(self, x, edge_index):
        x_initial = x  # Save the input features for the skip connection
        
        # First convolutional layer
        x = self.conv1(x, edge_index)
        x = F.elu(x)
        x = self.dropout(x)
        
        # Second convolutional layer
        x = self.conv2(x, edge_index)
        
        # Skip connection
        x_initial = self.projection(x_initial)
        x = x + x_initial
        x = F.elu(x)
        x = self.dropout(x)
        
        # Fully connected layers
        x = F.relu(self.fc1(x))
        x = self.dropout(x)
        x = self.fc2(x)  # Output layer
        
        return x

In [17]:
def train_gnn(model, data, optimizer, num_epochs=500, patience=50):

    criterion = torch.nn.MSELoss()
    best_rmse = float('inf')
    epochs_without_improvement = 0
    # scheduler = StepLR(optimizer, step_size=10, gamma=0.1)
    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min', patience=10, factor=0.7, verbose=True)

    for epoch in range(num_epochs):
        model.train()
        optimizer.zero_grad()

        # Training step
 
        x = data.x.to(device)
        edge_index = data.edge_index.to(device)
        y = data.y.to(device)

        # Use only the nodes indicated by the train_mask
        out = model(x, edge_index)
        loss = criterion(out[train_mask].squeeze(), y[train_mask])
        loss.backward()
        optimizer.step()

        # Evaluation step
        model.eval()
        with torch.no_grad():
            val_out = model(x, edge_index)
            val_predictions = val_out[val_mask].squeeze().cpu().detach().numpy()
            true_values = y[val_mask].cpu().numpy()

            # Compute RMSE on validation set
            rmse = root_mean_squared_error(true_values, val_predictions)

        print(f"Epoch {epoch+1}/{num_epochs}, Loss: {loss.item():.4f}, RMSE: {rmse:.4f}")

        scheduler.step(rmse)

        # Early stopping check
        if rmse < best_rmse:
            best_rmse = rmse
            epochs_without_improvement = 0
        else:
            epochs_without_improvement += 1
            if epochs_without_improvement >= patience:
                print(f"Early stopping at epoch {epoch+1}")
                break

    return best_rmse

def objective(params):
    hidden_dim1 = int(params['hidden_dim1'])
    hidden_dim2 = int(params['hidden_dim2'])
    dropout_rate = params['dropout_rate']
    lr = params['lr']
    weight_decay = params['weight_decay']
    conv_type = params['conv_type']  # Added GNN type

    model = GNNModel(
        in_channels=dataset[0].num_node_features,
        hidden_channel1=hidden_dim1,
        hidden_channel2=hidden_dim2,
        dropout=dropout_rate,
        conv_type=conv_type  # Pass the selected GNN type
    ).to(device)

    optimizer = torch.optim.Adam(model.parameters(), lr=lr, weight_decay=weight_decay)
    

    # Train the model and get validation RMSE
    val_rmse = train_gnn(model, dataset[0], optimizer, num_epochs=500, patience=20)

    return val_rmse  # Minimizing the RMSE loss

# Define hyperparameter space
space = {
    'hidden_dim1': hp.quniform('hidden_dim1', 64, 512, 16),  # Expanded upper range for hidden_dim1
    'hidden_dim2': hp.quniform('hidden_dim2', 32, 256, 16),  # Expanded range for hidden_dim2
    'dropout_rate': hp.choice('dropout_rate', [0.2, 0.25, 0.3, 0.35, 0.4]),  # Adjusted dropout range
    'lr': hp.loguniform('lr', -5, -1),  # Fine-tuned learning rate range
    'weight_decay': hp.loguniform('weight_decay', -5, -1),  # Narrowed weight decay range
    'conv_type': hp.choice('conv_type', ["SAGEConv","GCNConv", "GATConv"]),  # GNN types
}

# Run hyperparameter optimization
trials = Trials()

best_params = fmin(
    fn=objective,
    space=space,
    algo=tpe.suggest,
    max_evals=400,
    trials=trials
)

print("Best hyperparameters found:", best_params)


  0%|          | 0/400 [00:00<?, ?trial/s, best loss=?]

INFO:hyperopt.tpe:build_posterior_wrapper took 0.002000 seconds
INFO:hyperopt.tpe:TPE using 0 trials


Epoch 1/500, Loss: 66.7454, RMSE: 6.2697               
Epoch 2/500, Loss: 90.1425, RMSE: 45.7526              
Epoch 3/500, Loss: 3059.6665, RMSE: 1514.3085          
Epoch 4/500, Loss: 2306126.0000, RMSE: 76.1382         
Epoch 5/500, Loss: 7405.9395, RMSE: 63.5255            
Epoch 6/500, Loss: 4488.0615, RMSE: 70.2783            
Epoch 7/500, Loss: 5502.3638, RMSE: 108.1788           
Epoch 8/500, Loss: 14210.0527, RMSE: 123.4926          
Epoch 9/500, Loss: 17963.8457, RMSE: 21.9855           
Epoch 10/500, Loss: 1747.8508, RMSE: 19.7780           
Epoch 11/500, Loss: 894.3483, RMSE: 18.3864            
Epoch 12/500, Loss: 873.8693, RMSE: 7.3414             
Epoch 13/500, Loss: 203.2678, RMSE: 5.9238             
Epoch 14/500, Loss: 122.9112, RMSE: 7.8390             
Epoch 15/500, Loss: 132.4001, RMSE: 9.3931             
Epoch 16/500, Loss: 150.1971, RMSE: 8.4336             
Epoch 17/500, Loss: 133.9453, RMSE: 6.2311             
Epoch 18/500, Loss: 100.9254, RMSE: 5.5496      

INFO:hyperopt.tpe:build_posterior_wrapper took 0.000997 seconds
INFO:hyperopt.tpe:TPE using 1/1 trials with best loss 5.549550


Epoch 1/500, Loss: 66.4794, RMSE: 149.4397                                       
Epoch 2/500, Loss: 44033.7188, RMSE: 222.3687                                    
Epoch 3/500, Loss: 107552.2500, RMSE: 6120.4219                                  
Epoch 4/500, Loss: 39597456.0000, RMSE: 5096.7227                                
Epoch 5/500, Loss: 27134924.0000, RMSE: 174.5485                                 
Epoch 6/500, Loss: 48012.5781, RMSE: 896.3345                                    
Epoch 7/500, Loss: 983481.8750, RMSE: 6.5341                                     
Epoch 8/500, Loss: 36061.7773, RMSE: 8.0700                                      
Epoch 9/500, Loss: 20932.7344, RMSE: 44.7144                                     
Epoch 10/500, Loss: 255922.5156, RMSE: 6.5539                                    
Epoch 11/500, Loss: 57352.4258, RMSE: 6.5496                                     
Epoch 12/500, Loss: 8988.4980, RMSE: 6.5457                                      
Epoch 13/500, Lo

...

Epoch 1/500, Loss: 66.7499, RMSE: 6.1066                                          
Epoch 2/500, Loss: 61.0858, RMSE: 5.6514                                          
Epoch 3/500, Loss: 55.2592, RMSE: 5.5339                                          
Epoch 4/500, Loss: 53.6498, RMSE: 5.7312                                          
Epoch 5/500, Loss: 55.2897, RMSE: 5.5213                                          
Epoch 6/500, Loss: 52.8804, RMSE: 5.4334                                          
Epoch 7/500, Loss: 52.3077, RMSE: 5.4809                                          
Epoch 8/500, Loss: 52.6928, RMSE: 5.4788                                          
Epoch 9/500, Loss: 52.9708, RMSE: 5.4081                                          
Epoch 10/500, Loss: 51.6822, RMSE: 5.3287                                         
Epoch 11/500, Loss: 50.6000, RMSE: 5.3261                                         
Epoch 12/500, Loss: 50.0727, RMSE: 5.3461                                         
Epoc

INFO:hyperopt.tpe:build_posterior_wrapper took 0.001997 seconds
INFO:hyperopt.tpe:TPE using 398/398 trials with best loss 2.607473


Epoch 1/500, Loss: 68.6450, RMSE: 5.9375                                          
Epoch 2/500, Loss: 58.8297, RMSE: 22.9993                                         
Epoch 3/500, Loss: 566.0402, RMSE: 5.5120                                         
Epoch 4/500, Loss: 52.7202, RMSE: 6.3715                                          
Epoch 5/500, Loss: 63.8149, RMSE: 5.7442                                          
Epoch 6/500, Loss: 56.0076, RMSE: 5.7931                                          
Epoch 7/500, Loss: 55.7213, RMSE: 5.6512                                          
Epoch 8/500, Loss: 54.8436, RMSE: 5.3859                                          
Epoch 9/500, Loss: 51.0591, RMSE: 5.3842                                          
Epoch 10/500, Loss: 51.0283, RMSE: 5.2835                                         
Epoch 11/500, Loss: 49.7018, RMSE: 5.2240                                         
Epoch 12/500, Loss: 50.1030, RMSE: 5.2002                                         
Epoc

INFO:hyperopt.tpe:build_posterior_wrapper took 0.001001 seconds
INFO:hyperopt.tpe:TPE using 399/399 trials with best loss 2.607473


Epoch 1/500, Loss: 67.4557, RMSE: 5.6085                                          
Epoch 2/500, Loss: 54.5017, RMSE: 9.5290                                          
Epoch 3/500, Loss: 110.1885, RMSE: 5.4534                                         
Epoch 4/500, Loss: 51.8571, RMSE: 5.9743                                          
Epoch 5/500, Loss: 58.8369, RMSE: 5.8935                                          
Epoch 6/500, Loss: 58.1059, RMSE: 5.5466                                          
Epoch 7/500, Loss: 53.5730, RMSE: 5.5773                                          
Epoch 8/500, Loss: 52.4969, RMSE: 5.4848                                          
Epoch 9/500, Loss: 52.4098, RMSE: 5.6707                                          
Epoch 10/500, Loss: 55.9713, RMSE: 5.2434                                         
Epoch 11/500, Loss: 49.8751, RMSE: 5.5543                                         
Epoch 12/500, Loss: 52.6445, RMSE: 5.2414                                         
Epoc